## 18.12.18: eat the frog!
make full loop, process all the route files
generate the main gtfs files : routes.txt, trips.txt, stop_times.txt

In [1]:
import pandas as pd
from openpyxl import load_workbook
import time,datetime
from collections import OrderedDict
import json

make a hierarchical loop, that goes through:  
- routes
- weekday / sunday
- directions

In [2]:
stopsFile = 'stops_simple.csv'
outputFolder = 'gtfs/'

In [3]:
configDict = json.load(open('hmrl-config.json','r'))

In [4]:
configDict
# we'll only be using the needed routes info for now, a lot of other stuff here is from the static-gtfs-manager wizard

{'routes': [{'route_id': 'RED',
   'route_sequence': ['AME',
    'SRN',
    'ESI',
    'ERA',
    'BTN',
    'MSP',
    'BLR',
    'KUK',
    'KPH',
    'JNT',
    'MYP'],
   'direction_suffix': ['2', '1'],
   'route_short_name': 'Red',
   'route_long_name': 'Miyapur to LB Nagar',
   'route_color': 'E31E24',
   'route_text_color': 'FFFFFF'},
  {'route_id': 'BLU',
   'route_sequence': ['AME',
    'BEG',
    'PRN',
    'ROP',
    'PAR',
    'PRG',
    'SEC',
    'MET',
    'TAR',
    'HSG',
    'NGR',
    'SOI',
    'UPL',
    'NAG'],
   'direction_suffix': ['2', '1'],
   'route_short_name': 'Blue',
   'route_long_name': 'Nagole to Ameerpet',
   'route_color': '0081BF',
   'route_text_color': 'FFFFFF'}],
 'route_type': 1,
 'agency_id': 'HMRL',
 'agency_name': 'Hyderabad Metro Rail Limited',
 'agency_url': 'http://hmrl.telangana.gov.in/',
 'agency_timezone': 'Asia/Kolkata',
 'stopsCSV': 'hydcsv_related/stops_simple.csv',
 'missingStopsCSV': 'hydcsv_related/missing-stops-rules.csv',
 'repl

In [5]:
# put in the csv files in the main dict
for route in configDict.get('routes',[]):
    if route.get('route_id','') == 'RED':
        route['files'] = [['red-wk-0.csv','red-wk-1.csv'],['red-su-0.csv','red-su-1.csv']]
    elif route.get('route_id','') == 'BLU':
        route['files'] = [['blu-wk-0.csv','blu-wk-1.csv'],['blu-su-0.csv','blu-su-1.csv']]

In [6]:
# load the stop codes
stopsDF = pd.read_csv(stopsFile) #.dropna(subset=['order_RED']).sort_values('order_RED')

In [7]:
'#'*100

'####################################################################################################'

## custom functions

In [8]:
def boilDownHeader(x):
    '''
    Aim: to convert table headers like 'MYP1 - A', 'KHA1 -D' to 'MYP_arrival', 'KHA_departure'
    '''
    sep = '-' if '-' in x else None

    y = x.split(sep)[0].strip() # take first word
    if y[-1].isdigit(): y = y[:-1] # remove number if present at end
    
    if x.split(sep)[-1].strip().upper().startswith('A'):
        y += '_arrival'
    elif x.split(sep)[-1].strip().upper().startswith('D'):
        y += '_departure'
    return y

#testing:
print(boilDownHeader("""AME 2
DEP""")) # headers with line break
print(boilDownHeader('MYP1 - A')) # with space
print(boilDownHeader('KHA1-A')) # without space
print(boilDownHeader('KHA1 -D')) # partial space


AME_departure
MYP_arrival
KHA_arrival
KHA_departure


In [9]:
'#'*100

'####################################################################################################'

In [10]:
def findTimings(df,tripN=0, stop_id='MYP'):
    arrival = ''
    departure = ''
    
    if stop_id+'_departure' in df.columns:
        departure = df[stop_id+'_departure'].iloc[tripN].strip()
        # there was an error encountered here earlier because of a mis-named column.. may happen again
        
    if stop_id+'_arrival' in df.columns:
        arrival = df[stop_id+'_arrival'].iloc[tripN].strip()
        if not len(departure): departure = arrival # last stops like AME in Blue line have no departure column.

    # print(tripN,stop_id,arrival,departure)
    return [arrival,departure]

In [11]:
'#'*100

'####################################################################################################'

In [30]:
def stopLookup(stopsDF, stop_id='MYP'):
    filterStopsDF = stopsDF[ stopsDF['stop_id'] == stop_id ].reset_index(drop=True)
    if len(filterStopsDF): 
        return filterStopsDF.stop_name.iloc[0]
    
    #else..
    return '(stop not found)'
#test:
print('MYP:', stopLookup(stopsDF, 'MYP'))
print('LBN:', stopLookup(stopsDF, 'LBN'))
print('ola:', stopLookup(stopsDF, 'ola'))

MYP: Miyapur
LBN: L B Nagar
ola: (stop not found)


In [11]:
'#'*100

'####################################################################################################'

# main loop

In [13]:
# initialize
routesCollector = []
tripsCollector = []
stopTimesCollector = []

In [14]:
for routeNum, route in enumerate( configDict.get('routes',[]) ):
    # 1st loop : routes
    route_id = route.get('route_id','R'+str(routeNum) )
    routeRow = OrderedDict({
        'route_id': route_id,
        'agency_id': configDict.get('agency_id',''),
        'route_short_name': route.get('route_short_name',''),
        'route_long_name': route.get('route_long_name',''),
        'route_type': configDict.get('route_type',1),
        'route_color': route.get('route_color',''),
        'route_text_color': route.get('route_text_color',''),
    })
    routesCollector.append(routeRow)
    
    for serviceN, service_id in enumerate( ['WK','SU'] ):
        # 2nd loop: service (weekday / sunday)
       
        for direction_id in range(2):
            # 3rd loop: direction
            print()
            print(route_id, service_id, direction_id, route['files'][serviceN][direction_id])
            
            # get the suitable stops list
            
            orderFlag = True if direction_id == 0 else False
            # reverse it if it's return journey
            stopsList = stopsDF.dropna(subset=['order_{}'.format(route_id)])\
                .sort_values(by='order_{}'.format(route_id), ascending=orderFlag)\
                .stop_id.tolist()
            print(stopsList)
            
            #########################################
            # load the DATA for the specific route + service + direction combination
            dataFile = route['files'][serviceN][direction_id]
            # total 8 data files to traverse
            
            # debugging: skip other files
            # if dataFile != 'blu-su-1.csv':
            #    continue 
                        
            df = pd.read_csv(dataFile, dtype=str, skip_blank_lines=True).fillna('')\
                .rename(columns=lambda x: boilDownHeader(x))
            # 
            
            for tripN in range(len(df)):
                # 4th loop : cycle through each line (aka trip) in data file
                trip_id = '{}.{}.{}.{}.'.format(route_id,service_id,direction_id, str(tripN).rjust(3,'0')) 
                # still one more part left: timing. That will happen in stop times loop
                # adding a serial number because there are some cases of identical timings in the same route+direction.
                
                tripRow = OrderedDict({
                    'route_id': route_id,
                    'service_id': service_id,
                    'trip_id': trip_id, 
                    'trip_headsign': '', #placeholder, populate this after stop times loop
                    'direction_id': str(direction_id),
                    'shape_id': '{}_{}'.format(routeRow['route_id'],direction_id)
                }) # made a row for this trip. CSV data file has 1 trip per line.

                
                sequence = 0
                for stop_id in stopsList:
                    # 5th loop: cycle through each stop in the supposed sequence for this trip
                    
                    # outsourcing getting timings to a custom function
                    foundTimings = findTimings(df,tripN, stop_id) 
                    # should get [t1,t2] array, else ['',''] if this trip does not serve this stop.
                    # passing whole dataframe in with the row number
                    
                    if tripN % 100 == 0:
                        # print timings from every 1st and 100th trip
                        print(dataFile,tripN,stop_id,foundTimings[0],foundTimings[1])
                    
                    if foundTimings != ['','']:
                        sequence += 1
                        if sequence == 1: 
                            trip_id = trip_id + foundTimings[0][:2] + foundTimings[0][3:5] 
                            # so if '07:39:00', suffix '0739' to trip_id
                            tripRow['trip_id'] = trip_id
                        
                        stopTimeRow = OrderedDict({
                            'trip_id': trip_id,
                            'arrival_time': foundTimings[0],
                            'departure_time': foundTimings[1],
                            'stop_id': stop_id,
                            'stop_sequence': sequence,
                            'timepoint': 0
                        })
                        
                        stopTimesCollector.append(stopTimeRow)
                
                # trip_headsign: take the last stop in the iteration that had a valid timing
                tripRow['trip_headsign'] = stopLookup(stopsDF, stopTimeRow['stop_id']) 
                
                if sequence > 0:
                    tripsCollector.append(tripRow) 
                    # add trip row after trip_id has been set
                    # and if any stops at all have been added



RED WK 0 red-wk-0.csv
['MYP', 'JNT', 'KPH', 'KUK', 'BLR', 'MSP', 'BTN', 'ERA', 'ESI', 'SRN', 'AME', 'PUN', 'IRM', 'KHA', 'LKP', 'ASM', 'NAM', 'GAB', 'OMC', 'MGB', 'MKL', 'NEM', 'MSB', 'DSN', 'CHP', 'VOM', 'LBN']
red-wk-0.csv 0 MYP  
red-wk-0.csv 0 JNT  
red-wk-0.csv 0 KPH  
red-wk-0.csv 0 KUK  
red-wk-0.csv 0 BLR  
red-wk-0.csv 0 MSP  
red-wk-0.csv 0 BTN  
red-wk-0.csv 0 ERA  
red-wk-0.csv 0 ESI  
red-wk-0.csv 0 SRN  
red-wk-0.csv 0 AME  
red-wk-0.csv 0 PUN  
red-wk-0.csv 0 IRM  
red-wk-0.csv 0 KHA  
red-wk-0.csv 0 LKP  
red-wk-0.csv 0 ASM  
red-wk-0.csv 0 NAM  
red-wk-0.csv 0 GAB  
red-wk-0.csv 0 OMC  
red-wk-0.csv 0 MGB 06:29:20 06:30:00
red-wk-0.csv 0 MKL 06:31:24 06:31:49
red-wk-0.csv 0 NEM 06:33:55 06:34:20
red-wk-0.csv 0 MSB 06:35:47 06:36:12
red-wk-0.csv 0 DSN 06:38:06 06:38:36
red-wk-0.csv 0 CHP 06:40:05 06:40:30
red-wk-0.csv 0 VOM 06:42:12 06:42:37
red-wk-0.csv 0 LBN 06:44:34 06:44:59
red-wk-0.csv 100 MYP 18:04:35 18:05:00
red-wk-0.csv 100 JNT 18:07:21 18:07:46
red-wk-0.csv 1

blu-wk-0.csv 100 NAG 18:16:30 18:17:00
blu-wk-0.csv 100 UPL 18:18:32 18:18:52
blu-wk-0.csv 100 STD 18:20:40 18:20:55
blu-wk-0.csv 100 NGRI 18:22:32 18:22:47
blu-wk-0.csv 100 HSG 18:24:18 18:24:33
blu-wk-0.csv 100 TAR 18:26:45 18:27:00
blu-wk-0.csv 100 MET 18:28:50 18:29:10
blu-wk-0.csv 100 SEC 18:32:22 18:32:42
blu-wk-0.csv 100 PRG 18:35:30 18:35:45
blu-wk-0.csv 100 PAR 18:37:23 18:37:38
blu-wk-0.csv 100 RSP 18:39:03 18:39:18
blu-wk-0.csv 100 PRN 18:41:19 18:41:34
blu-wk-0.csv 100 BEG 18:44:04 18:44:34
blu-wk-0.csv 100 AME 18:49:10 18:49:10

BLU WK 1 blu-wk-1.csv
['AME', 'BEG', 'PRN', 'RSP', 'PAR', 'PRG', 'SEC', 'MET', 'TAR', 'HSG', 'NGRI', 'STD', 'UPL', 'NAG']
blu-wk-1.csv 0 AME 06:29:10 06:30:00
blu-wk-1.csv 0 BEG 06:34:48 06:35:13
blu-wk-1.csv 0 PRN 06:37:33 06:37:48
blu-wk-1.csv 0 RSP 06:39:43 06:39:58
blu-wk-1.csv 0 PAR 06:41:25 06:41:40
blu-wk-1.csv 0 PRG 06:43:15 06:43:30
blu-wk-1.csv 0 SEC 06:46:14 06:46:34
blu-wk-1.csv 0 MET 06:49:44 06:50:04
blu-wk-1.csv 0 TAR 06:51:46 06:52:

In [17]:
'#'*100

'####################################################################################################'

# make and preview tables

In [15]:
routesDF = pd.DataFrame(routesCollector)

In [16]:
routesDF

route_id agency_id route_short_name      route_long_name  route_type  \
0      RED      HMRL              Red  Miyapur to LB Nagar           1   
1      BLU      HMRL             Blue   Nagole to Ameerpet           1   

  route_color route_text_color  
0      E31E24           FFFFFF  
1      0081BF           FFFFFF

In [17]:
'#'*100

'####################################################################################################'

In [18]:
tripsDF = pd.DataFrame(tripsCollector)
len(tripsDF)

1052

In [19]:
tripsDF.sample(20)

route_id service_id            trip_id trip_headsign direction_id shape_id
71       RED         WK  RED.WK.0.071.1427     L B Nagar            0    RED_0
550      BLU         WK  BLU.WK.0.022.0841      Ameerpet            0    BLU_0
782      BLU         WK  BLU.WK.1.118.2046        Nagole            1    BLU_1
481      RED         SU  RED.SU.1.078.1654       Miyapur            1    RED_1
510      RED         SU  RED.SU.1.107.2013       Miyapur            1    RED_1
458      RED         SU  RED.SU.1.055.1350       Miyapur            1    RED_1
112      RED         WK  RED.WK.0.112.1922     L B Nagar            0    RED_0
860      BLU         SU  BLU.SU.0.062.1443      Ameerpet            0    BLU_0
747      BLU         WK  BLU.WK.1.083.1652        Nagole            1    BLU_1
648      BLU         WK  BLU.WK.0.120.2026      Ameerpet            0    BLU_0
413      RED         SU  RED.SU.1.010.0750       Miyapur            1    RED_1
832      BLU         SU  BLU.SU.0.034.1059      Ameerpet            0    BLU_0
328      RED         SU  RED.SU.0.053.1323     L B Nagar            0    RED_0
239      RED         WK  RED.WK.1.101.1829       Miyapur            1    RED_1
68       RED         WK  RED.WK.0.068.1403     L B Nagar            0    RED_0
570      BLU         WK  BLU.WK.0.042.1051      Ameerpet            0    BLU_0
2        RED         WK  RED.WK.0.002.0629     L B Nagar            0    RED_0
110      RED         WK  RED.WK.0.110.1909     L B Nagar            0    RED_0
422      RED         SU  RED.SU.1.019.0902       Miyapur            1    RED_1
362      RED         SU  RED.SU.0.087.1745     L B Nagar            0    RED_0

In [20]:
'#'*100

'####################################################################################################'

In [21]:
stopTimesDF = pd.DataFrame(stopTimesCollector)
len(stopTimesDF)

21396

In [22]:
stopTimesDF.sample(20)

trip_id arrival_time departure_time stop_id  stop_sequence  \
19692  BLU.SU.1.005.0740     07:52:25       07:52:40     PAR              5   
12770  RED.SU.1.077.1646     17:08:44       17:09:09     NAM             11   
3105   RED.WK.0.117.1955     20:06:08       20:06:33     MSP              6   
13288  RED.SU.1.096.1902     19:35:55       19:36:20     PUN             16   
10702  RED.SU.0.127.2245     22:58:27       22:58:52     BTN              7   
10340  RED.SU.0.113.2034     21:19:05       21:19:30     MSB             23   
2906   RED.WK.0.109.1903     19:48:05       19:48:30     MSB             23   
5183   RED.WK.1.057.1246     13:21:32       13:22:12     AME             17   
5079   RED.WK.1.053.1214     12:56:43       12:57:08     BTN             21   
861    RED.WK.0.034.0948     09:53:36       09:54:06     KPH              3   
19104  BLU.SU.0.090.1809     18:17:18       18:17:33     HSG              5   
17992  BLU.SU.0.010.0747     08:15:04       08:15:34     BEG             13   
9637   RED.SU.0.087.1745     18:28:13       18:28:38     NEM             22   
20063  BLU.SU.1.031.1108     11:37:02       11:37:17     STD             12   
7781   RED.SU.0.019.0851     08:54:21       08:54:46     JNT              2   
16310  BLU.WK.1.023.0920     09:53:10       09:53:40     NAG             14   
15505  BLU.WK.0.102.1829     18:41:50       18:42:10     MET              7   
17338  BLU.WK.1.097.1829     18:43:45       18:44:00     PRG              6   
8083   RED.SU.0.030.1019     10:32:27       10:32:52     BTN              7   
17134  BLU.WK.1.082.1644     17:13:02       17:13:17     STD             12   

       timepoint  
19692          0  
12770          0  
3105           0  
13288          0  
10702          0  
10340          0  
2906           0  
5183           0  
5079           0  
861            0  
19104          0  
17992          0  
9637           0  
20063          0  
7781           0  
16310          0  
15505          0  
17338          0  
8083           0  
17134          0

In [24]:
'#'*100

'####################################################################################################'

## write the gtfs files

In [23]:
routesDF.to_csv(outputFolder+'routes.txt',index=False)
tripsDF.to_csv(outputFolder+'trips.txt',index=False)
stopTimesDF.to_csv(outputFolder+'stop_times.txt',index=False)

In [24]:
'#'*100

'####################################################################################################'

#### rough work

In [25]:
'34'.rjust(3,'0')

'034'

In [26]:
'3456'.rjust(3,'0')

'3456'

In [27]:
'asdf'.ljust(10)

'asdf      '